## Auto mode

This is for testing propouses

In [1]:
import pickle
from collections import defaultdict

from config import Color
from helpers import clean  #, local2global
from helpers.change_coordinates import GRAs_to_ENUs
from mavlink.customtypes.location import ENUPose, GRAPose
from plan import Plan
from simulator import (
    QGC,
    ConfigGazebo,
    ConfigQGC,
    ConfigVis,
    Gazebo,
    NoneVisualizer,
    Simulator,
)
from simulator.gazebo.config import GazVehicle
from simulator.QGroundControl.config import QGCTraj

clean()

## Simulation Configuration

In [2]:
gra_origin = GRAPose(-35.3633280, 149.1652241, 0, 90)   # east, north, up, heading
enu_origin = ENUPose(0, 0, gra_origin.alt, gra_origin.heading) 

base_homes= ENUPose.list([  # east, north, up, heading
    (0., 15., 0., 30.),
    (15., 0., 0., 0),
    (-15., -15., 0., 0),
    (-15., 0., 0., 45),
    (5., -20., 0., 0.),
])
base_paths = [Plan.create_square_path(side_len=10, alt=5,heading=0) for _ in base_homes]

colors=[
    Color.BLUE,
    Color.BLUE,
    Color.BLUE,
    Color.RED,
    Color.RED,
]


## Assign vehicles to GCS (by color)
gcs_sysids: dict[str, list[int]] = defaultdict(list)

for i,color in enumerate(colors,start=1):
    gcs_sysids[f'{color.name} {color.emoji}'].append(i)

## Gazebo Congiguration

In [3]:
gaz_config = ConfigGazebo(origin = enu_origin,
                          world_path="simulator/gazebo/worlds/runway.world")

for path,home,c in zip(base_paths,base_homes,colors):
    gaz_config.add(base_path=path,base_home=home,color=c)
gaz_config.show()

## QGroundControl Configuration

In [4]:
qgc_config = ConfigQGC(origin = gra_origin)

for path,home,color in zip(base_paths,base_homes,colors):
    qgc_config.add(base_path=path,base_home=home,color=color)
qgc_config.show()

# No Simulator

In [5]:
novis_config = ConfigVis[int]()

for i,_ in enumerate(base_homes):
    novis_config.add_vehicle(i)

## Visualizers

In [6]:
novis=NoneVisualizer(novis_config)

gaz= Gazebo(gaz_config,gra_origin)

qgc=QGC(qgc_config)

## Launch Simulatotion

In [7]:
simulator = Simulator(
	visualizers=[qgc],
	gcs_sysids=gcs_sysids,
	missions=[veh.mission for veh in qgc_config.vehicles],
	verbose=2,
)

orac = simulator.launch()

🚀 ArduPilot SITL vehicle 1 launched (PID 2198393)
🚀 ArduPilot SITL vehicle 3 launched (PID 2198400)
🚀 UAV logic for vehicle 3 launched (PID 2198405)
🚀 ArduPilot SITL vehicle 5 launched (PID 2198406)
🚀 Proxy for vehicle 3 launched (PID 2198408)
🚀 UAV logic for vehicle 5 launched (PID 2198409)
🚀 ArduPilot SITL vehicle 4 launched (PID 2198404)
🚀 UAV logic for vehicle 1 launched (PID 2198395)
🚀 ArduPilot SITL vehicle 2 launched (PID 2198398)
🚀 Proxy for vehicle 1 launched (PID 2198418)
🚀 UAV logic for vehicle 4 launched (PID 2198414)
🚀 UAV logic for vehicle 2 launched (PID 2198419)
🚀 Proxy for vehicle 4 launched (PID 2198425)
🚀 Proxy for vehicle 2 launched (PID 2198427)
🚀 Proxy for vehicle 5 launched (PID 2198412)
[Errno 111] Connection refused sleeping
[Errno 111] Connection refused sleeping
🚀 Starting Proxy 1
🚀 Starting Proxy 2
[Errno 111] Connection refused sleeping
🚀 Starting Proxy 5
🔗 UAV logic 5 is connected to Oracle ⚪
✅ Heartbeat received
Logic 🧠 5: 🚀 lauching
Vehicle 5: ▶️ Plan St

Vehicle 4: ▶️ Step Started: clear uav missions


## Oracle checking

In [8]:
while len(orac.conns):
    for sysid in list(orac.conns.keys()):
        if orac.is_plan_done(sysid):
            orac.remove(sysid)

Vehicle 5: 🧹 Cleared previous mission
Vehicle 5: ✅ Step Done: clear uav missions
Vehicle 5: ✅ 7 waypoints read.
Vehicle 5: 🧭 Mission[0] → cmd: WAYPOINT, x: -35.3632831, y: 149.1654444, z: 0.0, current: 0
Vehicle 5: 🧭 Mission[1] → cmd: TAKEOFF, x: -35.3632831, y: 149.1654444, z: 5.0, current: 0
Vehicle 5: 🧭 Mission[2] → cmd: WAYPOINT, x: -35.3632831, y: 149.1653343, z: 5.0, current: 0
Vehicle 5: 🧭 Mission[3] → cmd: WAYPOINT, x: -35.3631933, y: 149.1653343, z: 5.0, current: 0
Vehicle 5: 🧭 Mission[4] → cmd: WAYPOINT, x: -35.3631933, y: 149.1654444, z: 5.0, current: 0
Vehicle 5: 🧭 Mission[5] → cmd: WAYPOINT, x: -35.3632831, y: 149.1654444, z: 5.0, current: 0
Vehicle 5: 🧭 Mission[6] → cmd: LAND, x: -35.3632831, y: 149.1654444, z: 0.0, current: 0
Vehicle 3: 🧹 Cleared previous mission
Vehicle 3: ✅ Step Done: clear uav missions
Vehicle 3: ✅ 7 waypoints read.
Vehicle 3: 🧭 Mission[0] → cmd: WAYPOINT, x: -35.3634627, y: 149.1653893, z: 0.0, current: 0
Vehicle 3: 🧭 Mission[1] → cmd: TAKEOFF, x: -3

## Print Positions gathered

In [9]:
import time

from config import DATA_PATH
from helpers.change_coordinates import GRA

qgs_colors = list(dict.fromkeys(colors))
for gcs_name,color in zip(gcs_sysids,qgs_colors):
    enu_trajs = []
    gcsplt_config = ConfigGazebo(origin = enu_origin,world_path="")
    mtrajs:list[QGCTraj] = []
    filepath =  DATA_PATH / f"trajectories_{gcs_name}.pkl"
    while not filepath.exists():
        time.sleep(0.1)  # wait 100ms
    with open(filepath, "rb") as f:
        trajs = pickle.load(f)
    for sysid,path in trajs.items():
        mtraj = ConfigGazebo.create_mtraj(
            traj=GRAs_to_ENUs(GRA(*gra_origin[:3]), path),
            color=color
        )
        gcsplt_config.add_vehicle(
            GazVehicle(
                model="",
                color=color,
                home=ENUPose(0,0,0,0),
                mtraj=mtraj)
            )
    gcsplt_config.show()


📤 GCS ← UAV 4: Sending DONE (attempt 2)
GCS RED 🟥: ✅ Vehicle 4 completed its mission
✅ All UAVs assigned to GCS RED 🟥 have completed their mission.
✅ ACK received. DONE message acknowledged.
❎ Vehicle 4 logic stopped.
💾 Trajectories saved to '/home/abeldg/uav-cyber-sim/data/trajectories_RED 🟥.pkl'.
Connection reset or closed by peer on TCP socket
❎ Proxy 4 stopped.
